In [1]:
from visual_behavior import utilities as vbu
import visual_behavior.plotting as vbp
from visual_behavior.utilities import EyeTrackingData
from visual_behavior import database as db
import pandas as pd
import matplotlib.pyplot as plt
import os
import numpy as np
import time
import seaborn as sns
import matplotlib.patches as patches

from plotly.subplots import make_subplots
import plotly.graph_objects as go
import plotly.express as px

from scipy import stats

from multiprocessing import Pool

from dro.modules import eye_tracking as et
from dro.modules import plotting as plot_utils

import chart_studio.tools as tls

import warnings
warnings.filterwarnings("ignore")

In [104]:
import plotly.io as pio
pio.renderers.default='notebook'

In [2]:
%matplotlib notebook
%widescreen

In [3]:
manifest = pd.read_csv('/allen/programs/braintv/workgroups/nc-ophys/Doug/2019.12.10.sessions_with_tracking.csv')
sessions_to_exclude = pd.read_csv('/allen/programs/braintv/workgroups/nc-ophys/visual_behavior/2019.12.10_eye_tracking_sessions_to_exclude.csv')
manifest = manifest[~manifest['ophys_session_id'].isin(sessions_to_exclude['sessions_to_exclude'].tolist())]

additional_sessions_to_exclude = [
    960475393, #mislabeled session name
]
manifest = manifest[~manifest['ophys_session_id'].isin(additional_sessions_to_exclude)]

In [4]:
eye_dict = {}
pool = Pool(16)
osids = manifest['ophys_session_id'].unique()
ans = pool.map(et.open_eye_data,osids)
eye_dict = {d.ophys_session_id:d for d in ans if d is not None}

opening eye data for osid = 961226856
opening eye data for osid = 955991376
opening eye data for osid = 948042811
opening eye data for osid = 959454463
opening eye data for osid = 938359348
opening eye data for osid = 940775208
opening eye data for osid = 954961790
opening eye data for osid = 935859569
opening eye data for osid = 942114744
opening eye data for osid = 929255931
opening eye data for osid = 932664150
opening eye data for osid = 931687751
opening eye data for osid = 922743776
opening eye data for osid = 925478114
opening eye data for osid = 928142719
opening eye data for osid = 921922878
opening eye data for osid = 947199653
opening eye data for osid = 920317769
opening eye data for osid = 923704003
opening eye data for osid = 929255311
opening eye data for osid = 935559843
opening eye data for osid = 929688369
opening eye data for osid = 958931715
opening eye data for osid = 954981981
opening eye data for osid = 960593969
opening eye data for osid = 952434025
opening eye 

Process ForkPoolWorker-5:
Process ForkPoolWorker-9:
Process ForkPoolWorker-8:
Process ForkPoolWorker-13:
Process ForkPoolWorker-3:
Process ForkPoolWorker-16:
Process ForkPoolWorker-2:
Process ForkPoolWorker-4:
Process ForkPoolWorker-7:
Process ForkPoolWorker-11:
Process ForkPoolWorker-1:
Process ForkPoolWorker-6:
Process ForkPoolWorker-15:
Process ForkPoolWorker-12:
Process ForkPoolWorker-10:
Process ForkPoolWorker-14:
Traceback (most recent call last):
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/process.py", line 297, in _bootstrap
    self.run()
Traceback (most recent call last):
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/process.py", line 99, in run
    self._target(*self._args, **self._kwargs)
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/pool.py", line 110, in worker
    task = get()
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/process.py", line 297

  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/queues.py", line 351, in get
    with self._rlock:
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/queues.py", line 351, in get
    with self._rlock:
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/queues.py", line 351, in get
    with self._rlock:
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/queues.py", line 351, in get
    with self._rlock:
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/synchronize.py", line 95, in __enter__
    return self._semlock.__enter__()
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/synchronize.py", line 95, in __enter__
    return self._semlock.__enter__()
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/queues.py", line 352, in get
    res = self._reader.recv_bytes()
  File "/home/dougo/.conda/envs/v

In [5]:
eye_dict.keys()

dict_keys([961226856, 960593969, 959751299, 959454463, 958931715, 957189583, 955991376, 954981981, 954408500, 954961790, 952434025, 948090163, 948042811, 947199653, 943299247, 942114744, 941300832, 940446507, 940775208, 939524851, 939526443, 938359348, 938140092, 937162622, 935859569, 935559843, 933439847, 932664150, 932662051, 931564063, 931687751, 929688369, 929686773, 929255931, 929255311, 928146339, 928142719, 927721370, 927787876, 925478114, 923704003, 923202821, 922743776, 922511481, 922168593, 921922878, 920317769, 920695792, 919432737, 919888953, 918719819, 918718550, 919041767, 918889065, 917498735, 916650386, 915587736, 915306390, 914797752, 914728054, 914639324, 914161594, 913834848, 913564409, 911719666, 910971181, 910739829, 908441202, 907991198, 907177554, 906968227, 906521029, 906299056, 902777219, 902884228, 901759468, 900802327, 898295293, 894204946, 893937838, 892217026, 889918231, 889179793, 888940531, 888190799, 884359468, 880753403, 879897824, 878918807, 876557230,

In [7]:
pool = Pool(16)
bd = pool.map(et.open_behavior_data,list(eye_dict.keys()))
behavior_dict = {d.ophys_session_id:d for d in bd if d is not None}

opening behavior data for osid = 940775208
opening behavior data for osid = 959454463
opening behavior data for osid = 955991376
opening behavior data for osid = 954961790
opening behavior data for osid = 935859569
opening behavior data for osid = 948042811
opening behavior data for osid = 928142719
opening behavior data for osid = 931687751
opening behavior data for osid = 925478114
opening behavior data for osid = 961226856
opening behavior data for osid = 929255931
opening behavior data for osid = 932664150
opening behavior data for osid = 922743776
opening behavior data for osid = 942114744
opening behavior data for osid = 938359348
opening behavior data for osid = 921922878
opening behavior data for osid = 960593969
opening behavior data for osid = 932662051
opening behavior data for osid = 939524851
opening behavior data for osid = 938140092
opening behavior data for osid = 947199653
opening behavior data for osid = 923704003
opening behavior data for osid = 920317769
opening beh

Process ForkPoolWorker-30:
Process ForkPoolWorker-23:
Process ForkPoolWorker-31:
Process ForkPoolWorker-32:
Process ForkPoolWorker-24:
Process ForkPoolWorker-20:
Process ForkPoolWorker-27:
Process ForkPoolWorker-28:
Process ForkPoolWorker-18:
Process ForkPoolWorker-29:
Process ForkPoolWorker-19:
Process ForkPoolWorker-26:
Process ForkPoolWorker-22:
Process ForkPoolWorker-25:
Process ForkPoolWorker-17:
Process ForkPoolWorker-21:
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/process.py", line 297, in _bootstrap
    self.run()
  File "/home/doug

  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/queues.py", line 351, in get
    with self._rlock:
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/queues.py", line 351, in get
    with self._rlock:
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/queues.py", line 351, in get
    with self._rlock:
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/queues.py", line 351, in get
    with self._rlock:
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/synchronize.py", line 95, in __enter__
    return self._semlock.__enter__()
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/synchronize.py", line 95, in __enter__
    return self._semlock.__enter__()
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/pool.py", line 110, in worker
    task = get()
  File "/home/dougo/.conda/envs/visual_behavior/lib

In [9]:
valid_osids = list(behavior_dict.keys())
len(valid_osids)

160

In [29]:
def get_first_stim(osid):
    print('getting first response for {}'.format(osid))
    first_pupil_responses,first_running_responses = et.get_individual_image_responses(eye_dict[osid],behavior_dict[osid],relative_to='first_presentations')
    data = {osid:{'pupil':first_pupil_responses,'running':first_running_responses}}
    return data
def get_last_stim(osid):
    print('getting last response for {}'.format(osid))
    last_pupil_responses,last_running_responses = et.get_individual_image_responses(eye_dict[osid],behavior_dict[osid],relative_to='last_presentations')
    data = {osid:{'pupil':last_pupil_responses,'running':last_running_responses}}
    return data

getting last response for 919432737
getting last response for 918718550
getting last response for 917498735
getting last response for 915306390
getting last response for 919041767
getting last response for 919888953
getting last response for 914639324
getting last response for 918889065
getting last response for 913564409
getting last response for 918719819
getting last response for 916650386
getting last response for 910739829
getting last response for 914797752
getting last response for 907177554
getting last response for 906299056
getting last response for 914161594
getting last response for 911719666
getting last response for 915587736
getting last response for 901759468
getting last response for 894204946
getting last response for 914728054
getting last response for 889918231
getting last response for 902777219
getting last response for 908441202
getting last response for 906968227
getting last response for 910971181
getting last response for 913834848
getting last response for 88

Process ForkPoolWorker-241:
Process ForkPoolWorker-200:
Process ForkPoolWorker-256:
Process ForkPoolWorker-176:
Process ForkPoolWorker-191:
Process ForkPoolWorker-249:
Process ForkPoolWorker-226:
Process ForkPoolWorker-246:
Process ForkPoolWorker-232:
Process ForkPoolWorker-137:
Process ForkPoolWorker-240:
Process ForkPoolWorker-188:
Process ForkPoolWorker-196:
Process ForkPoolWorker-254:
Process ForkPoolWorker-168:
Traceback (most recent call last):
Process ForkPoolWorker-213:
Process ForkPoolWorker-185:
Process ForkPoolWorker-178:
Process ForkPoolWorker-140:
Process ForkPoolWorker-233:
Process ForkPoolWorker-211:
Process ForkPoolWorker-201:
Process ForkPoolWorker-236:
Process ForkPoolWorker-219:
Process ForkPoolWorker-223:
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/queues.py", line 351, in get
    with self._rlock:
Process ForkPoolWorker-190:
Process ForkPoolWorker-243:
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/qu

  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/process.py", line 297, in _bootstrap
    self.run()
Traceback (most recent call last):
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/process.py", line 297, in _bootstrap
    self.run()
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/queues.py", line 351, in get
    with self._rlock:
Traceback (most recent call last):
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/process.py", line 297, in _bootstrap
    self.run()
Traceback (most recent call last):
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/process.py", line 99, in run
    self._target(*self._args, **self._kwargs)
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/process.py", line 297, in _bootstrap
    self.run()
Traceback (most recent call last):
  File "/home/dougo/.conda/envs/visual_behavior/lib/python

  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/process.py", line 297, in _bootstrap
    self.run()
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/process.py", line 99, in run
    self._target(*self._args, **self._kwargs)
KeyboardInterrupt
Traceback (most recent call last):
Traceback (most recent call last):
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/queues.py", line 351, in get
    with self._rlock:
Traceback (most recent call last):
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/synchronize.py", line 95, in __enter__
    return self._semlock.__enter__()
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/queues.py", line 351, in get
    with self._rlock:
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing

  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/process.py", line 297, in _bootstrap
    self.run()
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/synchronize.py", line 95, in __enter__
    return self._semlock.__enter__()
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/process.py", line 297, in _bootstrap
    self.run()
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/process.py", line 297, in _bootstrap
    self.run()
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/process.py", line 99, in run
    self._target(*self._args, **self._kwargs)
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/process.py", line 99, in run
    self._target(*self._args, **self._kwargs)
KeyboardInterrupt
Traceback (most recent call

...

  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/synchronize.py", line 95, in __enter__
    return self._semlock.__enter__()
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/synchronize.py", line 95, in __enter__
    return self._semlock.__enter__()
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/process.py", line 99, in run
    self._target(*self._args, **self._kwargs)
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/queues.py", line 351, in get
    with self._rlock:
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/synchronize.py", line 95, in __enter__
    return self._semlock.__enter__()
KeyboardInterrupt
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/synchronize.py", line 95, in __enter__
    return self._semlock.__enter__()
KeyboardInterrupt
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/mult

  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/pool.py", line 110, in worker
    task = get()
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/queues.py", line 351, in get
    with self._rlock:
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/pool.py", line 110, in worker
    task = get()
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/pool.py", line 110, in worker
    task = get()
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/queues.py", line 351, in get
    with self._rlock:
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/pool.py", line 110, in worker
    task = get()
KeyboardInterrupt
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/pool.py", line 110, in worker
    task = get()
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/pool.py", line 110, i

  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/queues.py", line 351, in get
    with self._rlock:
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/synchronize.py", line 95, in __enter__
    return self._semlock.__enter__()
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/queues.py", line 351, in get
    with self._rlock:
KeyboardInterrupt
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/pool.py", line 110, in worker
    task = get()
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/queues.py", line 351, in get
    with self._rlock:
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/queues.py", line 351, in get
    with self._rlock:
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/pool.py", line 110, in worker
    task = get()
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/

  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/queues.py", line 351, in get
    with self._rlock:
KeyboardInterrupt
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/synchronize.py", line 95, in __enter__
    return self._semlock.__enter__()
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/pool.py", line 110, in worker
    task = get()
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/queues.py", line 351, in get
    with self._rlock:
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/process.py", line 99, in run
    self._target(*self._args, **self._kwargs)
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/synchronize.py", line 95, in __enter__
    return self._semlock.__enter__()
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/synchronize.py", line 95, in __enter__
    return self._seml

KeyboardInterrupt
KeyboardInterrupt
KeyboardInterrupt
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/synchronize.py", line 95, in __enter__
    return self._semlock.__enter__()
KeyboardInterrupt
KeyboardInterrupt
KeyboardInterrupt
KeyboardInterrupt
KeyboardInterrupt
KeyboardInterrupt
KeyboardInterrupt
KeyboardInterrupt
KeyboardInterrupt
KeyboardInterrupt
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/process.py", line 99, in run
    self._target(*self._args, **self._kwargs)
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/queues.py", line 351, in get
    with self._rlock:
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/queues.py", line 351, in get
    with self._rlock:
  File "/home/dougo/.conda/envs/visual_behavior/lib/python3.7/multiprocessing/pool.py", line 110, in worker
    task = get()
KeyboardInterrupt
KeyboardInterrupt
  File "/home/dougo/.conda/envs/visual_b

In [42]:
pool = Pool(16)
first_response_list = pool.map(get_first_stim,list(valid_osids))
last_response_list = pool.map(get_last_stim,list(valid_osids))

getting first response for 959454463
getting first response for 961226856
getting first response for 940775208
getting first response for 955991376
getting first response for 954961790
getting first response for 931687751
getting first response for 948042811
getting first response for 942114744
getting first response for 935859569
getting first response for 938359348
getting first response for 928142719
getting first response for 922743776
getting first response for 925478114
getting first response for 929255931
getting first response for 932664150
getting first response for 921922878
getting first response for 929255311
getting first response for 929688369
getting first response for 923704003
getting first response for 927721370
getting first response for 935559843
getting first response for 929686773
getting first response for 952434025
getting first response for 939524851
getting first response for 947199653
getting first response for 920317769
getting first response for 954981981
g

getting last response for 879897824
getting last response for 916650386
getting last response for 873542787
getting last response for 860331718
getting last response for 911719666
getting last response for 914161594
getting last response for 884359468
getting last response for 918719819
getting last response for 902777219
getting last response for 914797752
getting last response for 855083235
getting last response for 893937838
getting last response for 906968227
getting last response for 908441202
getting last response for 900802327
getting last response for 889179793
getting last response for 863981645
getting last response for 915587736
getting last response for 880753403
getting last response for 910971181
getting last response for 902884228
getting last response for 892217026
getting last response for 878918807
getting last response for 898295293
getting last response for 888940531
getting last response for 907991198
getting last response for 913834848
getting last response for 91

In [81]:
response_dict = {}
# for respo
for condition,response_list in zip(['first','last'],[first_response_list,last_response_list]):
    response_dict[condition] = {}
    for response in response_list:
        osid = list(response.keys())[0]
        response_dict[condition][osid] = response[osid]


In [90]:
response_dfs = {
    'pupil':{'first':pd.DataFrame(),'last':pd.DataFrame()},
    'running':{'first':pd.DataFrame(),'last':pd.DataFrame()},
}
# iterate over response types (first = onset of stimulus, last = offset of stimulus)
for response_type in ['pupil','running']:
    for condition in ['first','last']:
        # iterate over every session id
        for osid in response_dict[condition].keys():
            # get mean response for each image ID, save to a dataframe with columns formatted as {IMAGE_ID}_{OSID}
            for image_id in response_dict[condition][osid][response_type].keys():
                df = response_dict[condition][osid][response_type][image_id]
                if len(response_dfs[response_type][condition]) == 0:
                    response_dfs[response_type][condition]['time'] = df['time']
                columns = [c for c in df.columns if c!='time']
                response_dfs[response_type][condition]['{}_osid={}'.format(image_id,osid)] = df[columns].mean(axis=1)

In [83]:
image_ids = np.sort(np.unique(np.array([c.split('_')[0] for c in response_dfs['pupil']['first'].columns if c.startswith('im')])))
image_ids

array(['im000', 'im031', 'im035', 'im045', 'im054', 'im061', 'im062',
       'im063', 'im065', 'im066', 'im069', 'im073', 'im075', 'im077',
       'im085', 'im106'], dtype='<U5')

In [91]:
response_dfs['pupil']['first'].head()

time  im061_osid=961226856  im062_osid=961226856  \
0 -15.000000             -0.017140              0.002832   
1 -14.983333             -0.016977              0.003963   
2 -14.966667             -0.015603              0.006040   
3 -14.950000             -0.012651              0.006644   
4 -14.933333             -0.010483              0.005910   

   im063_osid=961226856  im065_osid=961226856  im066_osid=961226856  \
0             -0.025369              0.015835             -0.028616   
1             -0.025625              0.015773             -0.027486   
2             -0.026045              0.016228             -0.026576   
3             -0.024398              0.018310             -0.025778   
4             -0.021435              0.019775             -0.025749   

   im069_osid=961226856  im077_osid=961226856  im085_osid=961226856  \
0              0.042538             -0.001265              0.013804   
1              0.042917             -0.000896              0.014605   
2              0.043950              0.000373              0.016260   
3              0.043092              0.000053              0.016741   
4              0.040890             -0.002013              0.018443   

   im061_osid=960593969  im062_osid=960593969  im063_osid=960593969  \
0             -0.051457              0.026145             -0.036697   
1             -0.050963              0.029562             -0.037549   
2             -0.047143              0.036152             -0.039145   
3             -0.043885              0.038270             -0.042239   
4             -0.040940              0.037202             -0.044435   

   im065_osid=960593969  im066_osid=960593969  im069_osid=960593969  \
0             -0.010767             -0.035865              0.041785   
1             -0.008919             -0.036625              0.040908   
2             -0.002632             -0.036621              0.038627   
3              0.003742             -0.033155              0.037483   
4              0.005618             -0.028293              0.038810   

   im077_osid=960593969  im085_osid=960593969  im061_osid=959751299  \
0              0.003416             -0.026683              0.020875   
1              0.002637             -0.025274              0.021813   
2              0.002204             -0.023823              0.022953   
3              0.007099             -0.023221              0.022868   
4              0.014580             -0.021117              0.021108   

   im062_osid=959751299  im063_osid=959751299  im065_osid=959751299  \
0             -0.005300             -0.002472              0.023280   
1             -0.004583             -0.002007              0.022899   
2             -0.004040             -0.001494              0.021872   
3             -0.004765             -0.000994              0.021840   
4             -0.003722             -0.001171              0.022312   

   im066_osid=959751299  im069_osid=959751299  im077_osid=959751299  \
0              0.021700              0.072549             -0.009643   
1              0.022824              0.072710             -0.009276   
2              0.024382              0.074696             -0.007685   
3              0.023945              0.077897             -0.003745   
4              0.024107              0.079052             -0.000523   

   im085_osid=959751299  im000_osid=959454463  im031_osid=959454463  \
0              0.048886              0.010020              0.041041   
1              0.049120              0.009846              0.040121   
2              0.050100              0.009574              0.038107   
3              0.053128              0.009495              0.035121   
4              0.056214              0.011208              0.035140   

   im035_osid=959454463  im045_osid=959454463  im054_osid=959454463  \
0             -0.023437              0.031883              0.034597   
1             -0.024311              0.030861              0.035256   
2             -0.0

In [149]:
for image_id in image_ids:
    print('image ID = {}'.format(image_id))
    subplot_titles = [
        'pupil response to {} onset'.format(image_id),
        'pupil response to {} offset'.format(image_id),
        'running response to {} onset'.format(image_id),
        'running response to {} offset'.format(image_id),
    ]
    fig = make_subplots(rows=2, cols=2, shared_xaxes=True, shared_yaxes=False,subplot_titles=subplot_titles)

    plotnumber = 0
    for row, response_type in enumerate(['pupil','running']):
        for col, condition in enumerate(['first','last']):
            plotnumber += 1
            df = response_dfs[response_type][condition]

            if row == 0 and col == 0:
                add_to_legend = True
            else:
                add_to_legend = False
            df_cols = [c for c in df.columns if c.startswith(image_id)]
            for df_col in df_cols:
                fig.add_trace(
                    go.Scatter(
                        x = df['time'],
                        y = df[df_col],
                        opacity=0.50,
                        showlegend=add_to_legend,
                        name='{}'.format(df_col.split('_')[1]),
                    ),
                    row=row+1, 
                    col=col+1,
                )
            fig.add_trace(
                go.Scatter(
                    x = df['time'],
                    y = df[df_cols].mean(axis=1),
                    opacity=1,
                    line = {'width':4,'color':'black'},
                    showlegend=add_to_legend,
                    name='grand average',
                ),
                row=row+1, 
                col=col+1,
            )
            if condition == 'first':
                plot_utils.designate_flashes_plotly(fig,omit=None,pre_color='gray',post_color='blue', plotnumbers=[plotnumber] ,lims=[-100,100], alpha=0.4)
            elif condition == 'last':
                plot_utils.designate_flashes_plotly(fig,omit=None,pre_color='blue',post_color='gray', plotnumbers=[plotnumber] ,lims=[-6,6], alpha=0.4)
            
            if response_type == 'pupil':
                fig.update_yaxes(title_text="fraction change\nin pupil area", range=[-0.15,0.15], row=row+1, col=col+1)
            elif response_type == 'running':
                fig.update_yaxes(title_text="running speed (cm/s)", range=[-5,60], row=row+1, col=col+1)
                
            fig.update_xaxes(range=[-5,5], row=row+1, col=col+1)
            fig.update_xaxes(title_text="time from first stimulus presentation (s)", row=row+1, col=col+1)

    fig.update_layout(
        title="Responses to {}\n(blue = image {}, gray = average over all other images in set)".format(image_id, image_id),
    )
    fig.write_html("/home/dougo/code/dougollerenshaw.github.io/figures_to_share/2020.01.15_pupil_running_responses_by_image/2020.01.15_responses_to_image_{}.html".format(image_id))
#     fig.show()


image ID = im000
image ID = im031
image ID = im035
image ID = im045
image ID = im054
image ID = im061
image ID = im062
image ID = im063
image ID = im065
image ID = im066
image ID = im069
image ID = im073
image ID = im075
image ID = im077
image ID = im085
image ID = im106


In [136]:
df_grand_averages = {
    'pupil':{'first':pd.DataFrame(),'last':pd.DataFrame()},
    'running':{'first':pd.DataFrame(),'last':pd.DataFrame()},
}

for image_id in image_ids:
    for row, response_type in enumerate(['pupil','running']):
        for col, condition in enumerate(['first','last']):
            plotnumber += 1
            
            df = response_dfs[response_type][condition]

            df_cols = [c for c in df.columns if c.startswith(image_id)]
            
            if len(df_grand_averages[response_type][condition]) == 0:
                df_grand_averages[response_type][condition]['time'] = df['time']
                
            df_grand_averages[response_type][condition][image_id] = df[df_cols].mean(axis=1)

image ID = im000
image ID = im031
image ID = im035
image ID = im045
image ID = im054
image ID = im061
image ID = im062
image ID = im063
image ID = im065
image ID = im066
image ID = im069
image ID = im073
image ID = im075
image ID = im077
image ID = im085
image ID = im106


In [146]:
image_set_A = [
    'im077',
    'im066',
    'im063',
    'im062',
    'im061',
    'im065',
    'im085',
    'im069',
]
image_set_B = [im for im in image_ids if im not in image_set_A]

In [156]:
sorted(image_set_B)

['im000', 'im031', 'im035', 'im045', 'im054', 'im073', 'im075', 'im106']

In [152]:
subplot_titles = [
    'pupil response to image onset',
    'pupil response to image offset',
    'running response to image onset',
    'running response to image offset',
] 
for image_set,image_set_name in zip([image_ids,image_set_A,image_set_B],['all','image set A','image set B']):
    fig = make_subplots(rows=2, cols=2, shared_xaxes=True, shared_yaxes=False,subplot_titles=subplot_titles)

    plotnumber = 0
    for row, response_type in enumerate(['pupil','running']):
        for col, condition in enumerate(['first','last']):
            plotnumber += 1
            df = df_grand_averages[response_type][condition]

            if row == 0 and col == 0:
                add_to_legend = True
            else:
                add_to_legend = False

            df_cols = [c for c in df.columns if c in image_set]
            for df_col in df_cols:
                fig.add_trace(
                    go.Scatter(
                        x = df['time'],
                        y = df[df_col],
                        opacity=0.6,
                        line = {'width':3},
                        showlegend=add_to_legend,
                        name=df_col,
                    ),
                    row=row+1, 
                    col=col+1,
                )
            fig.add_trace(
                go.Scatter(
                    x = df['time'],
                    y = df[df_cols].mean(axis=1),
                    opacity=1,
                    line = {'width':4,'color':'black'},
                    showlegend=add_to_legend,
                    name='grand average',
                ),
                row=row+1, 
                col=col+1,
            )
            if condition == 'first':
                plot_utils.designate_flashes_plotly(fig,omit=None,pre_color='gray',post_color='blue', plotnumbers=[plotnumber] ,lims=[-100,100], alpha=0.4)
            elif condition == 'last':
                plot_utils.designate_flashes_plotly(fig,omit=None,pre_color='blue',post_color='gray', plotnumbers=[plotnumber] ,lims=[-6,6], alpha=0.4)

            if response_type == 'pupil':
                fig.update_yaxes(title_text="fraction change\nin pupil area", range=[-0.05,0.05], row=row+1, col=col+1)
            elif response_type == 'running':
                fig.update_yaxes(title_text="running speed (cm/s)", range=[0,25], row=row+1, col=col+1)

            fig.update_xaxes(range=[-5,5], row=row+1, col=col+1)
            fig.update_xaxes(title_text="time from first stimulus presentation (s)", row=row+1, col=col+1)

    fig.update_layout(
        title="Responses to {}, averaged across sessions\n(blue = individual image, gray = average over all other images in set)".format(image_set_name),
    )
    fig.write_html("/home/dougo/code/dougollerenshaw.github.io/figures_to_share/2020.01.15_pupil_running_responses_by_image/2020.01.15_responses_averaged_across_sessions_{}.html".format(image_set_name.replace(' ','_')))
    fig.show()